# Import niezbędnych bibliotek

In [141]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from copy import copy

import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.offline as pyo

import yfinance as yf

%matplotlib inline

# Wczytywanie danych

In [142]:
aapl = pd.read_csv('data/aapl.csv', parse_dates=True, index_col=0)
# set Date column as index and remove it
aapl.index = pd.to_datetime(aapl.Date)
aapl.pop('Date')
aapl.head()

Open       High        Low      Close  Adj Close     Volume  \
Date                                                                           
2013-05-20  15.425357  15.921429  15.360714  15.818929  13.733949  451578400   
2013-05-21  15.648214  15.910000  15.507143  15.702143  13.632556  456022000   
2013-05-22  15.858929  16.012501  15.650714  15.762500  13.684957  443038400   
2013-05-23  15.569643  15.934286  15.563929  15.790714  13.709449  353021200   
2013-05-24  15.744643  15.916429  15.727143  15.898214  13.802786  276166800   

              Return  Log Return  
Date                              
2013-05-20       NaN         NaN  
2013-05-21 -0.007383   -0.007410  
2013-05-22  0.003844    0.003836  
2013-05-23  0.001790    0.001788  
2013-05-24  0.006808    0.006785

In [143]:
aapl.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 2516 entries, 2013-05-20 to 2023-05-16
Data columns (total 8 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Open        2516 non-null   float64
 1   High        2516 non-null   float64
 2   Low         2516 non-null   float64
 3   Close       2516 non-null   float64
 4   Adj Close   2516 non-null   float64
 5   Volume      2516 non-null   int64  
 6   Return      2515 non-null   float64
 7   Log Return  2515 non-null   float64
dtypes: float64(7), int64(1)
memory usage: 176.9 KB


# Wizualizacja analizowanych danych z wykorzystaniem biblioteki Plotly

1. Wykres nr 1 - Kursy cen akcji z pominięciem indeksu S&P500.

2. Wykres nr 2 - Kursy cen akcji wraz z indeksem S&P500.

3. Wykres nr 3 - Procentowe zmiany cen akcji.

Na wykresie można w łatwy sposób ograniczyć okres, dla którego dane są wyświetlane. Wystarczy zaznaczyć go myszą.

In [144]:
stocks = pd.read_csv('data/close_prices_clean.csv', parse_dates=True, index_col=0)
stocks_without_sp500 = copy(stocks)
stocks_without_sp500.pop('^GSPC')

fig = make_subplots(rows=3, cols=1)
for col in stocks_without_sp500.columns:
    fig.add_trace(go.Scatter(x=stocks_without_sp500.index, y=stocks_without_sp500[col], name=col), row=1, col=1)
for col in stocks.columns:
    fig.add_trace(go.Scatter(x=stocks.index, y=stocks[col], name=col), row=2, col=1)

returns_df = stocks.pct_change()
for col in returns_df.columns:
    fig.add_trace(go.Scatter(x=returns_df.index, y=returns_df[col], name=col), row=3, col=1)

fig.update_layout(height=800, width=2500, title_text="Wizualizacja danych z wykorzystaniem biblioteki Plotly", title_x=0.5)

fig.update_xaxes(title_text="Kursy cen akcji z pominięciem indeksu S&P500", row=1, col=1)
fig.update_xaxes(title_text="Kursy cen akcji wraz z indeksem S&P500", row=2, col=1)
fig.update_xaxes(title_text="Procentowe zmiany cen akcji", row=3, col=1)
fig.show()


# Wizualizacja danych spółki Apple - ostatnie 10 lat

1. Wykres nr 1 - atrybuty Open, Close, Adjusted Close, Low, High.

2. Wykres nr 2 - wykres Volume - ilości sprzedanych i kupionych danego dnia akcji.

3. Wykres nr 3 - wykres procentowych zmian kursu.

In [145]:
fig = make_subplots(rows=3, cols=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Adj Close'], name='Adj Close'), row=1, col=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Open'], name='Open'), row=1, col=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Close'], name='Close'), row=1, col=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['High'], name='High'), row=1, col=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Low'], name='Low'), row=1, col=1)

fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Volume'], name='Volume'), row=2, col=1)

fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Return'], name='Returns'), row=3, col=1)

fig.update_layout(height=600, width=1500, title_text="Apple Stock Prices")
fig.show()

# Close vs Adj Close - na przykładzie firmy 3M

Wykres przedstawiający różnicę pomiędzy kursem zamknięcia (Close), a dostosowanym kursem zamknięcia (Adjusted Close).

In [146]:
mmm = pd.read_csv('data/MMM.csv', parse_dates=True, index_col=0)
mmm.index = pd.to_datetime(mmm.Date)
mmm.pop('Date')
px.line(mmm, x=mmm.index, y=['Close', 'Adj Close'], title='Close and Adj Close prices')

# Simple Moving Average

### Wykres dla 2 ostatnich lat spółki Apple wraz ze wskaźnikami SMA_10 i SMA_50

In [147]:
aapl = pd.read_csv('data/aapl.csv', parse_dates=True, index_col=0)
aapl.index = pd.to_datetime(aapl.Date)
aapl = aapl.loc['2021-05-15':'2023-05-15']
aapl['SMA_10'] = aapl['Adj Close'].rolling(window=10).mean()
aapl['SMA_50'] = aapl['Adj Close'].rolling(window=50).mean()

fig = make_subplots(rows=1, cols=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['Adj Close'], name='Adj Close'), row=1, col=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['SMA_10'], name='SMA_10'), row=1, col=1)
fig.add_trace(go.Scatter(x=aapl.index, y=aapl['SMA_50'], name='SMA_50'), row=1, col=1)


fig.update_layout(height=600, width=1500, title_text="Apple Stock Prices")
fig.show()
